In [1]:
import pandas as pd
import numpy as np

from scipy.sparse import hstack, csr_matrix, vstack

from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import f1_score

from sklearn.ensemble import *
from sklearn.linear_model import *

from tqdm import *

import wordcloud
import matplotlib.pyplot as plt
import gc

import lightgbm as lgb
%matplotlib inline

In [44]:
from __future__ import print_function
from sklearn import metrics
from sklearn.pipeline import Pipeline
from sklearn.feature_extraction.text import CountVectorizer,TfidfTransformer
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.svm import LinearSVC
from sklearn.linear_model import LogisticRegression
# from sklearn.neural_network import MLPClassifier
# from sklearn.tree import DecisionTreeClassifier
# from sklearn.naive_bayes import MultinomialNB
# from sklearn.linear_model import SGDClassifier
# from sklearn.neighbors import KNeighborsClassifier
# from sklearn.ensemble import AdaBoostClassifier
# from sklearn.ensemble import RandomForestClassifier
import pandas as pd
from pyvi import ViTokenizer
import re
import string
import codecs

In [2]:
# Load data
train_df = pd.read_csv("./data/train.csv")
test_df = pd.read_csv("./data/test.csv")

In [3]:
train_df.head()

id                                            comment  label
0  train_000000  Dung dc sp tot cam on \nshop Đóng gói sản phẩm...      0
1  train_000001   Chất lượng sản phẩm tuyệt vời . Son mịn nhưng...      0
2  train_000002   Chất lượng sản phẩm tuyệt vời nhưng k có hộp ...      0
3  train_000003  :(( Mình hơi thất vọng 1 chút vì mình đã kỳ vọ...      1
4  train_000004  Lần trước mình mua áo gió màu hồng rất ok mà đ...      1

In [4]:
test_df.head()

id                                            comment
0  test_000000                        Chưa dùng thử nên chưa biết
1  test_000001   Không đáng tiềnVì ngay đợt sale nên mới mua n...
2  test_000002  Cám ơn shop. Đóng gói sản phẩm rất đẹp và chắc...
3  test_000003                      Vải đẹp.phom oki luôn.quá ưng
4  test_000004                            Chuẩn hàng đóng gói đẹp

In [62]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [63]:
test_df

id                                            comment
0      test_000000                        Chưa dùng thử nên chưa biết
1      test_000001   Không đáng tiềnVì ngay đợt sale nên mới mua n...
2      test_000002  Cám ơn shop. Đóng gói sản phẩm rất đẹp và chắc...
3      test_000003                      Vải đẹp.phom oki luôn.quá ưng
4      test_000004                            Chuẩn hàng đóng gói đẹp
5      test_000005   Đóng gói sản phẩm rất đẹp và chắc chắn Shop p...
6      test_000006  Sau khi đọc xong cuốn truyện thì cảm xúc...
7      test_000007  Chỉ cảm ứng khi gần dây điện ổ cắm ko có vật c...
8      test_000008  Tệ😡 Sản phẩm đứt chỉ tùm lum😡 Rách quá trời ch...
9      test_000009  Shop  Chất lượng sản phẩm rất kém Shop phục vụ...
10     test_000010                       Ad chỉ em cách chỉnh ngày vs
11     test_000011                                 Cắm phát nhận luôn
12     test_000012  Chất liệu tốt gói hàng chắc chắn sản phẩm chất...
13     test_000013  Da mình là hỗn hợp thiên dầu nhạy cảm  sau khi...
14     test_000014  Dù rep ib hơi chậm nhưng chất lượng sản phẩm k...
15     test_000015  Ban đầu mua về mẫu mã thì đẹp  nhưng không đượ...
16     test_000016   Chất lượng sản phẩm tuyệt vời Chất lượng sản ...
17     test_000017   Chất lượng sản phẩm tuyệt vời. Hàng test ra t...
18     test_000018   Chất lượng sản phẩm tuyệt vời 💖\nĐóng gói sản...
19     test_000019  Size hơi nhỏ so với số ký.  Chất lượng sản phẩ...
20     test_000020    Shop làm việc an tâmcó lòng vs hàng rất tốt....
21     test_000021  Shop chuyên chỉnh giá về 20k và lập nick rác đ...
22     test_000022  Giày cực kì ok.... Lúc đầu mua cũng sợ da bị h...
23     test_000023                                         Hơi bị mặn
24     test_000024  Sản phẩm mới mua mà đã mất vân tay.chơi game h...
25     test_000025  sản phẩm trên hình chỉ là minh họa chứ ngoài x...
26     test_000026  Yêu dã man luôn í. 5 màu màu nào cũng đẹp ko l...
27     test_000027                  Tien nao cua do tam chap nhan dc.
28     test_000028  Đồng hồ giống hình..nhỏ nhỏ xinh xinh... Đóng ...
29     test_000029  Phục vụ rất kém! Đã phân loại cho khách thì gi...
30     test_000030                               Xe hơi nhỏ cũng được
31     test_000031   Chất lượng sản phẩm tuyệt vờ.i Đóng gói sản p...
32     test_000032  Táo ăn vị ngọt thanh shop cân đủ một túi bị hở...
33     test_000033  Giày đẹp lắm nha. Đi chắc chân ♥️ cho shop ngh...
34     test_000034                                       Mẫu khăn xấu
35     test_000035   Chất lượng sản phẩm tuyệt vời Đóng gói sản ph...
36     test_000036  mình rõ ràng là mua bút chì kim bấm không hiểu...
37     test_000037  Giá cao so với thị trườngĐể giá sai \nGiảm 26%...
38     test_000038  Sau khi sử dụng khoảng 2 tháng mình thấy sản p...
39     test_000039  K tốt như cái cũ đã xài . Chất lượng sản phẩm ...
40     test_000040                          Che phủ kém nh vẫn cho 5*
41     test_000041  Minh thấy review em này đều bảo toner này dùng...
42     test_000042  Nơ đẹp ba lô đẹp dép đẹp mỗi tội hơi nhỏ do mẹ...
43     test_000043   Đóng gói sản phẩm rất kém bao bì bị rách khi ...
44     test_000044  Shop giao hàng lỗi liên hệ nhiều lần đồng ý nh...
45     test_000045    Chất lượng sản phẩm tuyệt vời\nSách hịn hay nữa
46     test_000046                      Mẫu mã đẹp đóng gói cẩn thận.
47     test_000047                                   Ao mong quan ok 
48     test_000048  "- đo nhịp tim phải để chế độ sport mới chính ...
49     test_000049   Chất lượng sản phẩm tuyệt vời. Mùi bơ thơm nh...
50     test_000050                  dây sạc ms nhận. nhưng dùng k đc.
51     test_000051  Đóng gói đẹp.cẩn thận nhưng chất lượng thì chá...
52     test_000052  Đặt lọ 155 k thì đi giao lọ kem khác giá 116k ...
53     test_000053   Chất lượng sản phẩm tuyệt vời. Rất là ưng ý l...
54     test_000054  Giao hàng bị lỗi. Màu không chính xác. Yêu cầu...
55     test_000055  quá tệ. giao hàng cũ mà còn bị hư không sử dụn...
56     test_000056   Chất 

In [5]:
print(train_df.info())
print(test_df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16087 entries, 0 to 16086
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   id       16087 non-null  object
 1   comment  16087 non-null  object
 2   label    16087 non-null  int64 
dtypes: int64(1), object(2)
memory usage: 377.2+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10981 entries, 0 to 10980
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   id       10981 non-null  object
 1   comment  10975 non-null  object
dtypes: object(2)
memory usage: 171.7+ KB
None


## Xác định emoji

In [8]:
pip install emoji

  Created wheel for emoji: filename=emoji-1.6.1-py3-none-any.whl size=169300 sha256=517a6f5be7b7aa716809b855ba09c28cea889130257a9294d0fdbf0b37012e8d
  Stored in directory: c:\users\cntt_manhnd\appdata\local\pip\cache\wheels\04\29\50\1e7189f03d2cf139e469863d54a1d3eabeb10c92c84e51f8a1
Successfully built emoji
Note: you may need to restart the kernel to use updated packages.


In [64]:
import emoji

def extract_emojis(s):
    return [c for c in s if c in emoji.UNICODE_EMOJI]

In [60]:
import emoji
import regex

def split_count(text):
    emoji_counter = 0
    data = regex.findall(r'\X', text)
    for word in data:
        if any(char in emoji.UNICODE_EMOJI for char in word):
            emoji_counter += 1
            # Remove from the given text the emojis
            text = text.replace(word, '') 

    words_counter = len(text.split())

    return emoji_counter, words_counter

In [61]:
line = "hello 👩🏾‍🎓 emoji hello 👨‍👩‍👦‍👦 how are 😊 you today🙅🏽🙅🏽"
counter = split_count(line)
print("Number of emojis - {}, number of words - {}".format(counter[0], counter[1]))

Number of emojis - 0, number of words - 10


In [65]:
extract_emojis("Quá đẹp so với giá 😍")

[]

In [ ]:
## Với comment tích cực

In [11]:
good_df = train_df[train_df['label'] == 0]
good_comment = good_df['comment'].values
good_emoji = []
for c in good_comment:
    good_emoji += extract_emojis(c)

good_emoji = np.unique(np.asarray(good_emoji))

In [12]:
good_emoji

array([], dtype=float64)

In [13]:
bad_df = train_df[train_df['label'] == 1]
bad_comment = bad_df['comment'].values

bad_emoji = []
for c in bad_comment:
    bad_emoji += extract_emojis(c)

bad_emoji = np.unique(np.asarray(bad_emoji))

In [14]:
bad_emoji

array([], dtype=float64)

## Chỉnh sửa lại 1 số teen code

In [32]:
str_mapping = {
    "ship": "vận chuyển",
    "shop": "cửa hàng",
    "m": "mình",
    "mik": "mình",
    "ko": "không",
    "k": " không ",
    "kh": "không",
    "khong": "không",
    "kg": "không",
    "khg": "không",
    "tl": "trả lời",
    "r": "rồi",
    "fb": "mạng xã hội", # facebook
    "face": "mạng xã hội",
    "thanks": "cảm ơn",
    "thank": "cảm ơn",
    "tks": "cảm ơn",
    "tk": "cảm ơn",
    "ok": "tốt",
    "dc": "được",
    "vs": "với",
    "đt": "điện thoại",
    "thjk": "thích",
    "qá": "quá",
    "trể": "trễ",
    "bgjo": "bao giờ",
    "sp": "sản phẩm"
}

In [33]:
def tokmap(tok):
    if tok.lower() in str_mapping:
        return str_mapping[tok.lower()]
    else:
        return tok

In [34]:
import re
def preprocess(cmt):
    cmt = re.sub(r"^\"*", "", cmt)
    cmt = re.sub(r"\"*$", "", cmt)
    tokens = cmt.split()
    tokens = map(tokmap, tokens)
    return " ".join(tokens)

In [35]:
train_df['comment'] = train_df['comment'].astype(str).fillna(' ')
train_df['comment'] = train_df['comment'].apply(lambda cmt: preprocess(cmt))

In [36]:
train_df

id                                            comment  label
0      train_000000  Dung được sản phẩm tot cam on cửa hàng Đóng gó...      0
1      train_000001  Chất lượng sản phẩm tuyệt vời . Son mịn nhưng ...      0
2      train_000002  Chất lượng sản phẩm tuyệt vời nhưng không có h...      0
3      train_000003  :(( Mình hơi thất vọng 1 chút vì mình đã kỳ vọ...      1
4      train_000004  Lần trước mình mua áo gió màu hồng rất tốt mà ...      1
...             ...                                                ...    ...
16082  train_016082  Chẳng biết là cửa hàng có biết đọc hay không m...      1
16083  train_016083  Cuốn này mỏng. Đọc một buổi sáng là hết. Thú t...      1
16084  train_016084                                  Mang êm chân. Đẹp      0
16085  train_016085  Tôi đã nhận đc hàng.Sau đây là vài lời muốn nó...      1
16086  train_016086            Hình vậy mà túi xấu quá kém chất lg quá      1

[16087 rows x 3 columns]

In [40]:
import string

In [46]:
VN_CHARS_LOWER = u'ạảãàáâậầấẩẫăắằặẳẵóòọõỏôộổỗồốơờớợởỡéèẻẹẽêếềệểễúùụủũưựữửừứíìịỉĩýỳỷỵỹđð'
VN_CHARS_UPPER = u'ẠẢÃÀÁÂẬẦẤẨẪĂẮẰẶẲẴÓÒỌÕỎÔỘỔỖỒỐƠỜỚỢỞỠÉÈẺẸẼÊẾỀỆỂỄÚÙỤỦŨƯỰỮỬỪỨÍÌỊỈĨÝỲỶỴỸÐĐ'
VN_CHARS = VN_CHARS_LOWER + VN_CHARS_UPPER
def no_marks(s):
    __INTAB = [ch for ch in VN_CHARS]
    __OUTTAB = "a"*17 + "o"*17 + "e"*11 + "u"*11 + "i"*5 + "y"*5 + "d"*2
    __OUTTAB += "A"*17 + "O"*17 + "E"*11 + "U"*11 + "I"*5 + "Y"*5 + "D"*2
    __r = re.compile("|".join(__INTAB))
    __replaces_dict = dict(zip(__INTAB, __OUTTAB))
    result = __r.sub(lambda m: __replaces_dict[m.group(0)], s)
    return result

def normalize_text(text):

    #Remove các ký tự kéo dài: vd: đẹppppppp
    text = re.sub(r'([A-Z])\1+', lambda m: m.group(1).upper(), text, flags=re.IGNORECASE)

    # Chuyển thành chữ thường
    text = text.lower()

    #Chuẩn hóa tiếng Việt, xử lý emoj, chuẩn hóa tiếng Anh, thuật ngữ
    replace_list = {
        'òa': 'oà', 'óa': 'oá', 'ỏa': 'oả', 'õa': 'oã', 'ọa': 'oạ', 'òe': 'oè', 'óe': 'oé','ỏe': 'oẻ',
        'õe': 'oẽ', 'ọe': 'oẹ', 'ùy': 'uỳ', 'úy': 'uý', 'ủy': 'uỷ', 'ũy': 'uỹ','ụy': 'uỵ', 'uả': 'ủa',
        'ả': 'ả', 'ố': 'ố', 'u´': 'ố','ỗ': 'ỗ', 'ồ': 'ồ', 'ổ': 'ổ', 'ấ': 'ấ', 'ẫ': 'ẫ', 'ẩ': 'ẩ',
        'ầ': 'ầ', 'ỏ': 'ỏ', 'ề': 'ề','ễ': 'ễ', 'ắ': 'ắ', 'ủ': 'ủ', 'ế': 'ế', 'ở': 'ở', 'ỉ': 'ỉ',
        'ẻ': 'ẻ', 'àk': u' à ','aˋ': 'à', 'iˋ': 'ì', 'ă´': 'ắ','ử': 'ử', 'e˜': 'ẽ', 'y˜': 'ỹ', 'a´': 'á',
        #Quy các icon về 2 loại emoj: Tích cực hoặc tiêu cực
        "👹": "nagative", "👻": "positive", "💃": "positive",'🤙': ' positive ', '👍': ' positive ',
        "💄": "positive", "💎": "positive", "💩": "positive","😕": "nagative", "😱": "nagative", "😸": "positive",
        "😾": "nagative", "🚫": "nagative",  "🤬": "nagative","🧚": "positive", "🧡": "positive",'🐶':' positive ',
        '👎': ' nagative ', '😣': ' nagative ','✨': ' positive ', '❣': ' positive ','☀': ' positive ',
        '♥': ' positive ', '🤩': ' positive ', 'like': ' positive ', '💌': ' positive ',
        '🤣': ' positive ', '🖤': ' positive ', '🤤': ' positive ', ':(': ' nagative ', '😢': ' nagative ',
        '❤': ' positive ', '😍': ' positive ', '😘': ' positive ', '😪': ' nagative ', '😊': ' positive ',
        '?': ' ? ', '😁': ' positive ', '💖': ' positive ', '😟': ' nagative ', '😭': ' nagative ',
        '💯': ' positive ', '💗': ' positive ', '♡': ' positive ', '💜': ' positive ', '🤗': ' positive ',
        '^^': ' positive ', '😨': ' nagative ', '☺': ' positive ', '💋': ' positive ', '👌': ' positive ',
        '😖': ' nagative ', '😀': ' positive ', ':((': ' nagative ', '😡': ' nagative ', '😠': ' nagative ',
        '😒': ' nagative ', '🙂': ' positive ', '😏': ' nagative ', '😝': ' positive ', '😄': ' positive ',
        '😙': ' positive ', '😤': ' nagative ', '😎': ' positive ', '😆': ' positive ', '💚': ' positive ',
        '✌': ' positive ', '💕': ' positive ', '😞': ' nagative ', '😓': ' nagative ', '️🆗️': ' positive ',
        '😉': ' positive ', '😂': ' positive ', ':v': '  positive ', '=))': '  positive ', '😋': ' positive ',
        '💓': ' positive ', '😐': ' nagative ', ':3': ' positive ', '😫': ' nagative ', '😥': ' nagative ',
        '😃': ' positive ', '😬': ' 😬 ', '😌': ' 😌 ', '💛': ' positive ', '🤝': ' positive ', '🎈': ' positive ',
        '😗': ' positive ', '🤔': ' nagative ', '😑': ' nagative ', '🔥': ' nagative ', '🙏': ' nagative ',
        '🆗': ' positive ', '😻': ' positive ', '💙': ' positive ', '💟': ' positive ',
        '😚': ' positive ', '❌': ' nagative ', '👏': ' positive ', ';)': ' positive ', '<3': ' positive ',
        '🌝': ' positive ',  '🌷': ' positive ', '🌸': ' positive ', '🌺': ' positive ',
        '🌼': ' positive ', '🍓': ' positive ', '🐅': ' positive ', '🐾': ' positive ', '👉': ' positive ',
        '💐': ' positive ', '💞': ' positive ', '💥': ' positive ', '💪': ' positive ',
        '💰': ' positive ',  '😇': ' positive ', '😛': ' positive ', '😜': ' positive ',
        '🙃': ' positive ', '🤑': ' positive ', '🤪': ' positive ','☹': ' nagative ',  '💀': ' nagative ',
        '😔': ' nagative ', '😧': ' nagative ', '😩': ' nagative ', '😰': ' nagative ', '😳': ' nagative ',
        '😵': ' nagative ', '😶': ' nagative ', '🙁': ' nagative ',
        #Chuẩn hóa 1 số sentiment words/English words
        ':))': '  positive ', ':)': ' positive ', 'ô kêi': ' ok ', 'okie': ' ok ', ' o kê ': ' ok ',
        'okey': ' ok ', 'ôkê': ' ok ', 'oki': ' ok ', ' oke ':  ' ok ',' okay':' ok ','okê':' ok ',
        ' tks ': u' cám ơn ', 'thks': u' cám ơn ', 'thanks': u' cám ơn ', 'ths': u' cám ơn ', 'thank': u' cám ơn ',
        '⭐': 'star ', '*': 'star ', '🌟': 'star ', '🎉': u' positive ',
        'kg ': u' không ','not': u' không ', u' kg ': u' không ', '"k ': u' không ',' kh ':u' không ','kô':u' không ','hok':u' không ',' kp ': u' không phải ',u' kô ': u' không ', '"ko ': u' không ', u' ko ': u' không ', u' k ': u' không ', 'khong': u' không ', u' hok ': u' không ',
        'he he': ' positive ','hehe': ' positive ','hihi': ' positive ', 'haha': ' positive ', 'hjhj': ' positive ',
        ' lol ': ' nagative ',' cc ': ' nagative ','cute': u' dễ thương ','huhu': ' nagative ', ' vs ': u' với ', 'wa': ' quá ', 'wá': u' quá', 'j': u' gì ', '“': ' ',
        ' sz ': u' cỡ ', 'size': u' cỡ ', u' đx ': u' được ', 'dk': u' được ', 'dc': u' được ', 'đk': u' được ',
        'đc': u' được ','authentic': u' chuẩn chính hãng ',u' aut ': u' chuẩn chính hãng ', u' auth ': u' chuẩn chính hãng ', 'thick': u' positive ', 'store': u' cửa hàng ',
        'shop': u' cửa hàng ', 'sp': u' sản phẩm ', 'gud': u' tốt ','god': u' tốt ','wel done':' tốt ', 'good': u' tốt ', 'gút': u' tốt ',
        'sấu': u' xấu ','gut': u' tốt ', u' tot ': u' tốt ', u' nice ': u' tốt ', 'perfect': 'rất tốt', 'bt': u' bình thường ',
        'time': u' thời gian ', 'qá': u' quá ', u' ship ': u' giao hàng ', u' m ': u' mình ', u' mik ': u' mình ',
        'ể': 'ể', 'product': 'sản phẩm', 'quality': 'chất lượng','chat':' chất ', 'excelent': 'hoàn hảo', 'bad': 'tệ','fresh': ' tươi ','sad': ' tệ ',
        'date': u' hạn sử dụng ', 'hsd': u' hạn sử dụng ','quickly': u' nhanh ', 'quick': u' nhanh ','fast': u' nhanh ','delivery': u' giao hàng ',u' síp ': u' giao hàng ',
        'beautiful': u' đẹp tuyệt vời ', u' tl ': u' trả lời ', u' r ': u' rồi ', u' shopE ': u' cửa hàng ',u' order ': u' đặt hàng ',
        'chất lg': u' chất lượng ',u' sd ': u' sử dụng ',u' dt ': u' điện thoại ',u' nt ': u' nhắn tin ',u' tl ': u' trả lời ',u' sài ': u' xài ',u'bjo':u' bao giờ ',
        'thik': u' thích ',u' sop ': u' cửa hàng ', ' fb ': ' facebook ', ' face ': ' facebook ', ' very ': u' rất ',u'quả ng ':u' quảng  ',
        'dep': u' đẹp ',u' xau ': u' xấu ','delicious': u' ngon ', u'hàg': u' hàng ', u'qủa': u' quả ',
        'iu': u' yêu ','fake': u' giả mạo ', 'trl': 'trả lời', '><': u' positive ',
        ' por ': u' tệ ',' poor ': u' tệ ', 'ib':u' nhắn tin ', 'rep':u' trả lời ',u'fback':' feedback ','fedback':' feedback ',
        #dưới 3* quy về 1*, trên 3* quy về 5*
        '6 sao': ' 5star ','6 star': ' 5star ', '5star': ' 5star ','5 sao': ' 5star ','5sao': ' 5star ',
        'starstarstarstarstar': ' 5star ', '1 sao': ' 1star ', '1sao': ' 1star ','2 sao':' 1star ','2sao':' 1star ',
        '2 starstar':' 1star ','1star': ' 1star ', '0 sao': ' 1star ', '0star': ' 1star ',}

    for k, v in replace_list.items():
        text = text.replace(k, v)

    # chuyen punctuation thành space
    translator = str.maketrans(string.punctuation, ' ' * len(string.punctuation))
    text = text.translate(translator)

    text = ViTokenizer.tokenize(text)
    texts = text.split()
    len_text = len(texts)

    texts = [t.replace('_', ' ') for t in texts]

    text = u' '.join(texts)

    #remove nốt những ký tự thừa thãi
    text = text.replace(u'"', u' ')
    text = text.replace(u'️', u'')
    text = text.replace('🏻','')
    return text

In [47]:
train_df['comment'] = train_df['comment'].apply(lambda cmt: normalize_text(cmt))

In [66]:
train_df['comment']

0        dung được sản phẩm tốt cam on cửa hàng đóng gó...
1        chất lượng sản phẩm tuyệt vời son mịn nhưng kh...
2        chất lượng sản phẩm tuyệt vời nhưng không có h...
3        nagative mình hơi thất vọng 1 chút vì mình đã ...
4        lần trước mình mua áo gió màu hồng rất tốt mà ...
5        chất lượng sản phẩm tuyệt vời có điều không cứ...
6        đã nhận được hàng rất nhanh mới đặt buổi tối m...
7        các siêu phẩm thấy cấu hình toàn tựa tựa nhau ...
8        hàng vận chuyển nhanh chất lượng tốt tư vấn nh...
9        đồng hồ đẹp nhưng 1 cái đứt dây 1 cái không ch...
10       chất lượng sản phẩm tuyệt vời y hình chụp đáng...
11       positive cửa hàng giao hàng nhanh quá đẹp lắm ...
12                                       nhìn đẹp phết nhỉ
13       đóng gói rất đẹp chất lượng sản phẩm rất tốt c...
14                           săn được với giá 11k toẹt vời
15                                        tốt rất hài lòng
16             giao thiếu mình cái này rồi cửa hàng ơi t

In [49]:
X_train, X_test, y_train, y_test = train_test_split(train_df.comment, train_df.label, test_size=0.3,random_state=42)

In [55]:
steps = []
stop_ws = (u'rằng',u'thì',u'là',u'mà')
steps.append(('CountVectorizer', CountVectorizer(ngram_range=(1,5),stop_words=stop_ws,max_df=0.5, min_df=5)))
steps.append(('tfidf', TfidfTransformer(use_idf=False, sublinear_tf = True,norm='l2',smooth_idf=True)))
steps.append(('classifier',  LinearSVC(fit_intercept = True,multi_class='crammer_singer', C=1)))
clf = Pipeline(steps)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)
report1 = metrics.classification_report(y_test, y_pred, labels=[1,0], digits=3)

In [56]:
clf.fit(X_train, y_train)
y_pred = clf.predict(X_train)
report2 = metrics.classification_report(y_train, y_pred, labels=[1,0], digits=3)

In [53]:
cross_score = cross_val_score(clf, X_train,y_train, cv=5)

In [58]:
#ERRO ANALYSIS
for id,x, y1, y2 in zip(train_df.id, X_train, y_train, y_pred):
    if y1 != y2:
        # CHECK EACH WRONG SAMPLE POSSITIVE/NAGATIVE
        if y1!=1:#0:
            print(id,x, y1, y2)

#CROSS VALIDATION
cross_score = cross_val_score(clf, X_train,y_train, cv=5)

#REPORT
print('DATASET LEN %d'%(len(X_train)))
print('TRAIN 70/30 \n\n',report1)
print('TRAIN OVERFITING\n\n',report2)
print("CROSSVALIDATION 5 FOLDS: %0.4f (+/- %0.4f)" % (cross_score.mean(), cross_score.std() * 2))

train_000103 quá dơ chua gi ma rai roi 0 1
train_000131 chất xấu lắm không ngấm nước 0 1
train_000145 nồi lấy về không nấu được không nóng không gì hết 0 1
train_000151 hũ nhựa có nắp kép ở trong sạch sẽ 0 1
train_000189 chất luomg qua kem 0 1
train_000200 sản phẩm không tương xứng với giá tiền quá xấu quá tệ không nên mua 0 1
train_000249 chất lượng sản phẩm rất kém nó còn bị bể nát hết 0 1
train_000250 giao sai 1mẫu 0 1
train_000395 thất vọng mua đồng hồ nhật mà nhận đồng hồ china 0 1
train_000418 sản phẩm tạm được hạt nhỏ lần này không ngon bằng lần trước 0 1
train_000512 son không lì lắm 0 1
train_000543 giày bị bung keo ở đế và có rất nhiều vết xước 0 1
train_000545 chất lượng bình thường không được như ý đúng là tiền nào của lấy đầu giầy bị móp không căng phồng giống hình 0 1
train_000571 không chất luong nhu hang xdesign 0 1
train_000583 cửa hàng e giao hàng chậm bình chỉ có 1 chế độ nấu chậm thôi không có còi báo 0 1
train_000608 dán ốp vào như là màn hình xài hoa văn vậy lần đ

DATASET LEN 11260
TRAIN 70/30 

               precision    recall  f1-score   support

           1      0.866     0.907     0.886      2036
           0      0.930     0.898     0.914      2791

    accuracy                          0.902      4827
   macro avg      0.898     0.903     0.900      4827
weighted avg      0.903     0.902     0.902      4827

TRAIN OVERFITING

               precision    recall  f1-score   support

           1      0.925     0.969     0.946      4771
           0      0.976     0.942     0.959      6489

    accuracy                          0.953     11260
   macro avg      0.951     0.955     0.953     11260
weighted avg      0.954     0.953     0.954     11260

CROSSVALIDATION 5 FOLDS: 0.8993 (+/- 0.0132)
